In [18]:
import pandas as pd
import matplotlib.pyplot as plt
from pandas.api.types import is_numeric_dtype
stack_dfs = pd.read_csv("StateGovFinances2005to2021.csv", index_col = ["State", "Year", "Format"], low_memory =False).sort_index()
panel_dfs_dict = {k:stack_dfs[stack_dfs.index.get_level_values(2)==k].reset_index().set_index(["State","Year"]).sort_index() for k in stack_dfs.index.get_level_values(2).unique()}
for key, df in panel_dfs_dict.items():
    for col in df.columns:
        if not is_numeric_dtype(df[col]):
            try:
                df[col] = pd.to_numeric(df[col], errors = "coerce")
                df[col] = df[col].fillna(0)
                df[col] = df[col].astype(int)
            except:
                pass
        else:
            df[col] = df[col].fillna("")



In [19]:

keys = ["GENERAL REVENUE","EXPENDITURE", "TAXES", "OTHER TAXES", "CURRENT CHARGES", "OTHER CHARGES", 'INDIVIDUAL INCOME', 'CORPORATE INCOME', "PROPERTY", "SPECIAL ASSESSMENTS",
        "SALES AND GROSS RECEIPTS", "GENERAL SALES", "MOTOR FUEL", "GAS SUPPLY", "EDUCATION", "HIGHER EDUCATION", "PUBLIC WELFARE"]	
keys = ["1" + k for k in keys]
plot_df = panel_dfs_dict['State & local government amount'][keys]
plot_df.rename(columns = {k:k.replace("1", "").title() for k in plot_df.keys()}, inplace = True)
plot_df["Total Income"] = plot_df["Individual Income"].add(plot_df["Corporate Income"])
plot_df["Deficit"] = plot_df["Expenditure"].sub(plot_df["General Revenue"])
pct_df = plot_df.apply(lambda x: x.div(plot_df["General Revenue"]) if is_numeric_dtype(x) else x)       

/tmp/ipykernel_5597/3057638026.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_5597/3057638026.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_5597/3057638026.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [20]:
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from plotly.subplots import make_subplots
from homebrewedFunctions.functions import *

In [21]:
corr_df = pct_df.groupby("State")[["Property", "Total Income"]].corr()["Property"]
corr_df[corr_df.index.get_level_values(1)=="Total Income"].mean()

-0.24406087843548963

In [22]:
pct_df

General Revenue  Expenditure     Taxes  Other Taxes  \
State Year                                                              
AK    2005-01-01              1.0     1.020571  0.299959     0.101606   
      2006-01-01              1.0     0.979468  0.332448     0.124330   
      2007-01-01              1.0     0.899085  0.381318     0.196027   
      2008-01-01              1.0     0.691497  0.538182     0.377388   
      2009-01-01              1.0     1.018409  0.457156     0.275097   
...                           ...          ...       ...          ...   
WY    2017-01-01              1.0     1.186696  0.320636     0.065916   
      2018-01-01              1.0     1.168497  0.332784     0.077058   
      2019-01-01              1.0     1.138575  0.368877     0.093729   
      2020-01-01              1.0     1.042102  0.310287     0.065064   
      2021-01-01              1.0     1.156654  0.306325     0.059361   

                  Current Charges  Other Charges  Individual Income  \
State Year                                                            
AK    2005-01-01         0.091275       0.024112                0.0   
      2006-01-01         0.087440       0.023981                0.0   
      2007-01-01         0.084775       0.021632                0.0   
      2008-01-01         0.061545       0.014074                0.0   
      2009-01-01         0.085806       0.021634                0.0   
...                           ...            ...                ...   
WY    2017-01-01         0.215106       0.020078                0.0   
      2018-01-01         0.219946       0.018857                0.0   
      2019-01-01         0.224958       0.019300                0.0   
      2020-01-01         0.192659       0.016152                0.0   
      2021-01-01         0.197044       0.018944                0.0   

                  Corporate Income  Property  Special Assessments  \
State Year                                                          
AK    2005-01-01          0.059919  0.090822             0.001281   
      2006-01-01          0.074538  0.087920             0.000767   
      2007-01-01          0.062753  0.079820             0.000711   
      2008-01-01          0.069533  0.057254             0.000389   
      2009-01-01          0.044256  0.084012             0.000430   
...                            ...       ...                  ...   
WY    2017-01-01          0.000000  0.142708             0.001196   
      2018-01-01          0.000000  0.129165             0.000849   
      2019-01-01          0.000000  0.136506             0.001017   
      2020-01-01          0.000000  0.124615             0.000999   
      2021-01-01          0.000000  0.127154             0.001023   

                  Sales And Gross Receipts  General Sales  Motor Fuel  \
State Year                                                              
AK    2005-01-01                  0.040721       0.016017    0.004027   
      2006-01-01                  0.039519       0.015546    0.003818   
      2007-01-01                  0.037334       0.013574    0.003031   
      2008-01-01                  0.030228       0.011503    0.002250   
      2009-01-01                  0.048817       0.025949    0.000705   
...                                    ...            ...         ...   
WY    2017-01-01                  0.101252       0.077704    0.013077   
      2018-01-01                  0.113324       0.089572    0.013107   
      2019-01-01                  0.124506       0.099926    0.013757   
      2020-01-01                  0.108050       0.086387    0.011873   
      2021-01-01                  0.106558       0.084037    0.011300   

                  Gas Supply  Education  Higher Education  Public Welfare  \
State Year                                                                  
AK    2005-01-01    0.000045   0.017785          0.055623        0.140687   
      2006-01-01    0.000040   0.016134          0.052503        

In [28]:
from homebrewedFunctions.functions import *
def line_dropdown(df):
    plot_df = df.reset_index()
    fig = px.line(plot_df, x="Year", y="Deficit", color="State")

    y_buttons = []
    for col in df.columns:
        if is_numeric_dtype(df[col]):
            y_buttons.append(
                dict(
                    args=[
                        {"y": [df.loc[state][col] for state in plot_df['State'].unique()]},
                        {"yaxis.title.text": col}
                    ],
                    label=col,
                    method="update"
                )
            )

    fig.update_layout(
        updatemenus=[
            dict(
                buttons=y_buttons,
                direction="down",
                showactive=True,
                x=0.17,
                xanchor="left",
                y=1.15,
                yanchor="top"
            ),
                    dict(
            type="buttons",
            direction="left",
            buttons=list([
                dict(
                    args=[{"yaxis.type": "linear"}],
                    label="Linear Y",
                    method="relayout"
                ),
                dict(
                    args=[{"yaxis.type": "log"}],
                    label="Log Y",
                    method="relayout"
                )
            ])
        ],

        annotations=[
            dict(
                text="Y-axis",
                x=0.32,
                xref="paper",
                y=1.25,
                yref="paper",
                xanchor="left",
                showarrow=False
            )
        ]
    )

    return fig
dfs = {"Levels": plot_df,
       "As Percent of General Revenue": pct_df}
figs = {key: line_dropdown(dataframe) for key, dataframe in dfs.items()}
fig = dict_of_figs_to_dropdown_fig(figs, show_fig = False,
                                 use_sliders = True)
fig.show()
fig.write_html(f"outputs/StateFinancesFigs.html")

# fig = line_dropdown(pct_df)
# fig.write_html("line_dropdown.html")

In [7]:
create_scatter_dropdown(pct_df, 
                        filename = "IncomePropertyAssessmentSalesFuelTaxesPctTotalRevenue.html", 
                        show_fig = True)



In [8]:
pct_df.values

array([[ 1.        ,  1.02057074,  0.29995929, ...,  0.14068692,
         0.05991931,  0.02057074],
       [ 1.        ,  0.97946762,  0.33244789, ...,  0.13096171,
         0.07453772, -0.02053238],
       [ 1.        ,  0.8990851 ,  0.38131764, ...,  0.11003663,
         0.06275343, -0.1009149 ],
       ...,
       [ 1.        ,  1.13857467,  0.36887743, ...,  0.10002334,
         0.        ,  0.13857467],
       [ 1.        ,  1.04210239,  0.31028664, ...,  0.08864143,
         0.        ,  0.04210239],
       [ 1.        ,  1.15665375,  0.30632528, ...,  0.09284819,
         0.        ,  0.15665375]])